## Rod Cantilever Example

In [1]:
import os
os.environ["MKL_THREADING_LAYER"] = "GNU" # for pardiso: if the kernel crashes, try changing "GNU" to "INTEL"

In [2]:
import numpy as np

import dismech

geom = dismech.GeomParams(rod_r0=0.001,
                          shell_h=0)

material = dismech.Material(density=1200,
                            youngs_rod=2e6,
                            youngs_shell=0,
                            poisson_rod=0.5,
                            poisson_shell=0)

static_2d_sim = dismech.SimParams(static_sim=False,
                                  two_d_sim=False,   # can change
                                  use_mid_edge=False,
                                  use_line_search=False,
                                  show_floor=False,
                                  log_data=True,
                                  log_step=1,
                                  dt=1e-2,
                                  max_iter=25,
                                  total_time=1.0,
                                  plot_step=1,
                                  tol=1e-4,
                                  ftol=1e-4,
                                  dtol=1e-2)

env = dismech.Environment()
env.add_force('gravity', g=np.array([0.0, 0.0, -9.81]))

geo = dismech.Geometry.from_txt(
    '../tests/resources/rod_cantilever/horizontal_rod_n21.txt')

robot = dismech.SoftRobot(geom, material, geo, static_2d_sim, env)

### Time Stepping

Contortion requires a simple moving boundary which is implemented as a before_step callback.

In [3]:
# Fix first 3 and last 3 nodes
fixed_points = np.array(
    np.where(robot.q[robot.node_dof_indices].reshape(-1, 3)[:, 0] <= 0.01)[0])
fixed_points1 = np.array(
    np.where(robot.q[robot.node_dof_indices].reshape(-1, 3)[:, 0] >= 0.09)[0])

robot = robot.fix_nodes(np.concat((fixed_points, fixed_points1)))


def move_and_twist(robot, t):
    """ Simple example of a moving boundary condition """
    u0 = 0.1
    w0 = 2

    # Create a copy to avoid modifying the previous value
    q = robot.q
    if t < 0.15:
        q[robot.map_node_to_dof(robot.fixed_nodes[:3])[
            :, 0]] += u0 * robot.sim_params.dt
    else:
        q[63:65] += w0 * robot.sim_params.dt
    return robot.update(q)


stepper = dismech.NewmarkBetaTimeStepper(robot)
stepper.before_step = move_and_twist

robots = stepper.simulate()

qs = np.stack([robot.q for robot in robots])

### Animation

The contortion is most visible from the side

In [5]:
%matplotlib notebook
from IPython.display import HTML

t = np.arange(robot.sim_params.total_time, step=robot.sim_params.dt)
options = dismech.AnimationOptions(y_lim=[-0.01, 0.01],
                  title='Contortion Cantilever (N=21)',
                  camera_view=(0,0))

ani = dismech.get_animation(robot, t, qs, options)
HTML(ani.to_jshtml())

<IPython.core.display.Javascript object>

In [ ]:
#ani.save('cantilever.gif', 'pillow')